In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

import seaborn as sns

import plotly.graph_objects as go
from statsmodels.tsa.arima_model import ARIMA

/usr/local/lib/python3.7/dist-packages/statsmodels/tools/_testing.py:19: FutureWarning:

pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.



# Data Loading

### About the data
#### The original data (iot_telemetry_data.csv) have data colleceted from three different devices ( Raspberry Pi) at different locations .This data set contains data from a specific device at particular location as the data had values for seconds which was creating lag and other issues while modelling, this data set is resampled by minute and contains 7 days of data.
i.e. **2020-07-12 00:01:00** to  **2020-07-20 00:03:00**  

In [ ]:
from google.colab import files
files.upload()

Saving data_device1.csv to data_device1.csv


{'data_device1.csv': b'Datetime,ts,co,humidity,light,lpg,motion,smoke,temp\r\n2020-07-12 00:01:00,1594512100.802322,0.00288910211688095,76.0,0.0,0.0051779326213540495,0.0,0.013451178918435301,19.700000762939453\r\n2020-07-12 00:02:00,1594512148.1063762,0.0028797897808176,75.93333435058594,0.0,0.005165932261533422,0.0,0.013417842755510466,19.744444529215496\r\n2020-07-12 00:03:00,1594512210.302688,0.0028673335511230995,76.06363539262252,0.0,0.0051497817009236,0.0,0.013373026815452216,19.76363615556197\r\n2020-07-12 00:04:00,1594512270.9825487,0.002837586942664566,76.09166526794434,0.0,0.005111089767544801,0.0,0.013265722086763148,19.75\r\n2020-07-12 00:05:00,1594512328.017501,0.002850886240125477,76.28888787163629,0.0,0.005128412691306801,0.0,0.013313751893965853,19.744444529215496\r\n2020-07-12 00:06:00,1594512387.3103964,0.0028346771842600598,76.02999954223633,0.0,0.0051072951334440704,0.0,0.013255203266465057,19.74000015258789\r\n2020-07-12 00:07:00,1594512451.0503547,0.0028259998894

In [ ]:
# loading data as dataframe
df = pd.read_csv("data_device1.csv")
df

Datetime            ts        co  ...  motion     smoke       temp
0      2020-07-12 00:01:00  1.594512e+09  0.002889  ...     0.0  0.013451  19.700001
1      2020-07-12 00:02:00  1.594512e+09  0.002880  ...     0.0  0.013418  19.744445
2      2020-07-12 00:03:00  1.594512e+09  0.002867  ...     0.0  0.013373  19.763636
3      2020-07-12 00:04:00  1.594512e+09  0.002838  ...     0.0  0.013266  19.750000
4      2020-07-12 00:05:00  1.594512e+09  0.002851  ...     0.0  0.013314  19.744445
...                    ...           ...       ...  ...     ...       ...        ...
11518  2020-07-19 23:59:00  1.595203e+09  0.003745  ...     0.0  0.016437  16.739999
11519  2020-07-20 00:00:00  1.595203e+09  0.003743  ...     0.0  0.016432  19.299999
11520  2020-07-20 00:01:00  1.595203e+09  0.003747  ...     0.0  0.016445  19.299999
11521  2020-07-20 00:02:00  1.595203e+09  0.003747  ...     0.0  0.016446  19.266666
11522  2020-07-20 00:03:00  1.595203e+09  0.003749  ...     0.0  0.016453  19.200001

[11523 rows x 9 columns]

In [ ]:
# making copy of the data
df_copy = df.copy(deep = True)
df_copy

Datetime            ts        co  ...  motion     smoke       temp
0      2020-07-12 00:01:00  1.594512e+09  0.002889  ...     0.0  0.013451  19.700001
1      2020-07-12 00:02:00  1.594512e+09  0.002880  ...     0.0  0.013418  19.744445
2      2020-07-12 00:03:00  1.594512e+09  0.002867  ...     0.0  0.013373  19.763636
3      2020-07-12 00:04:00  1.594512e+09  0.002838  ...     0.0  0.013266  19.750000
4      2020-07-12 00:05:00  1.594512e+09  0.002851  ...     0.0  0.013314  19.744445
...                    ...           ...       ...  ...     ...       ...        ...
11518  2020-07-19 23:59:00  1.595203e+09  0.003745  ...     0.0  0.016437  16.739999
11519  2020-07-20 00:00:00  1.595203e+09  0.003743  ...     0.0  0.016432  19.299999
11520  2020-07-20 00:01:00  1.595203e+09  0.003747  ...     0.0  0.016445  19.299999
11521  2020-07-20 00:02:00  1.595203e+09  0.003747  ...     0.0  0.016446  19.266666
11522  2020-07-20 00:03:00  1.595203e+09  0.003749  ...     0.0  0.016453  19.200001

[11523 rows x 9 columns]

## Data - Preprocessing

In [ ]:
# Setting Datetime column as index value
df_copy.set_index("Datetime", inplace=True)

In [ ]:
df_copy

ts        co  ...     smoke       temp
Datetime                                     ...                     
2020-07-12 00:01:00  1.594512e+09  0.002889  ...  0.013451  19.700001
2020-07-12 00:02:00  1.594512e+09  0.002880  ...  0.013418  19.744445
2020-07-12 00:03:00  1.594512e+09  0.002867  ...  0.013373  19.763636
2020-07-12 00:04:00  1.594512e+09  0.002838  ...  0.013266  19.750000
2020-07-12 00:05:00  1.594512e+09  0.002851  ...  0.013314  19.744445
...                           ...       ...  ...       ...        ...
2020-07-19 23:59:00  1.595203e+09  0.003745  ...  0.016437  16.739999
2020-07-20 00:00:00  1.595203e+09  0.003743  ...  0.016432  19.299999
2020-07-20 00:01:00  1.595203e+09  0.003747  ...  0.016445  19.299999
2020-07-20 00:02:00  1.595203e+09  0.003747  ...  0.016446  19.266666
2020-07-20 00:03:00  1.595203e+09  0.003749  ...  0.016453  19.200001

[11523 rows x 8 columns]

In [ ]:
ny_df = df_copy.reset_index()
ny_df.head(3)

Datetime            ts        co  ...  motion     smoke       temp
0  2020-07-12 00:01:00  1.594512e+09  0.002889  ...     0.0  0.013451  19.700001
1  2020-07-12 00:02:00  1.594512e+09  0.002880  ...     0.0  0.013418  19.744445
2  2020-07-12 00:03:00  1.594512e+09  0.002867  ...     0.0  0.013373  19.763636

[3 rows x 9 columns]

### Spliting the data

In [ ]:
train=df_copy[(df_copy.index >= '2020-07-12 00:01:00') & (df_copy.index <= '2020-07-17 00:01:00')]
test=df_copy[(df_copy.index > '2020-07-17 00:01:00')]

In [ ]:
train.shape

(7201, 8)

In [ ]:
test.shape

(4322, 8)

# Temperature Model Training and forecasting

In [ ]:
from statsmodels.tsa.arima_model import ARIMA
temp_model = ARIMA(train["temp"], order = (1,0,1), freq="Min")
temp_model_fit = temp_model.fit()

In [ ]:
temp_model_fit.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                              ARMA Model Results                              
==============================================================================
Dep. Variable:                   temp   No. Observations:                 7201
Model:                     ARMA(1, 1)   Log Likelihood                1212.685
Method:                       css-mle   S.D. of innovations              0.204
Date:                Mon, 12 Jul 2021   AIC                          -2417.370
Time:                        09:40:50   BIC                          -2389.842
Sample:                    07-12-2020   HQIC                         -2407.898
                         - 07-17-2020                                         
==============================================================================
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
const         19.3249      0.089    217.329      0.000      19.151      19.499
ar.L1.temp     0.9958      0.001    871.826      0.000       0.994       0.998
ma.L1.temp    -0.8398      0.008   -102.154      0.000      -0.856      -0.824
                                    Roots                                    
=============================================================================
                  Real          Imaginary           Modulus         Frequency
-----------------------------------------------------------------------------
AR.1            1.0042           +0.0000j            1.0042            0.0000
MA.1            1.1908           +0.0000j            1.1908            0.0000
-----------------------------------------------------------------------------
"""

In [ ]:
# Forecasting for validation on test data
forecast = pd.DataFrame(temp_model_fit.predict(start=7201, end = 11522),columns=['temp_forecast'])
forecast

temp_forecast
2020-07-17 00:02:00      19.566303
2020-07-17 00:03:00      19.565286
2020-07-17 00:04:00      19.564273
2020-07-17 00:05:00      19.563264
2020-07-17 00:06:00      19.562260
...                            ...
2020-07-19 23:59:00      19.324936
2020-07-20 00:00:00      19.324936
2020-07-20 00:01:00      19.324936
2020-07-20 00:02:00      19.324936
2020-07-20 00:03:00      19.324936

[4322 rows x 1 columns]

In [ ]:
forecasted_df = pd.concat([test['temp'],forecast["temp_forecast"]], axis=1, join="inner")

In [ ]:
forecasted_df

temp  temp_forecast
2020-07-17 00:02:00  19.700001      19.566303
2020-07-17 00:03:00  19.700001      19.565286
2020-07-17 00:04:00  19.710001      19.564273
2020-07-17 00:05:00  19.710001      19.563264
2020-07-17 00:06:00  19.788888      19.562260
...                        ...            ...
2020-07-19 23:59:00  16.739999      19.324936
2020-07-20 00:00:00  19.299999      19.324936
2020-07-20 00:01:00  19.299999      19.324936
2020-07-20 00:02:00  19.266666      19.324936
2020-07-20 00:03:00  19.200001      19.324936

[4322 rows x 2 columns]

In [ ]:
import plotly.graph_objects as go

fig = go.Figure()

# Add traces
fig.add_trace(go.Scatter(x=forecasted_df.index , y=forecasted_df["temp"],
                    mode='lines+markers',
                     name='Actual Temperature '))
fig.add_trace(go.Scatter(x=forecasted_df.index  , y= forecasted_df["temp_forecast"],
                     mode='lines+markers',
                     name='Forecasted Temperature'))



fig.update_layout(
    title="Actual Vs Forecasted Temperature ",
    xaxis_title="Days ",
    yaxis_title= "Temperature",
    font=dict(
        family="Courier New, monospace",
        size=18,
        color="RebeccaPurple"
    )
)

fig.show()

In [ ]:
# fig = px.line(s, x ="DateTime", y="AmbientLightSensor", title = "AmbientLightSensor")

# fig.update_xaxes(rangeslider_visible = True)
# fig.show()

In [ ]:
# Accuracy metrics
from statsmodels.tsa.stattools import acf

def forecast_accuracy(forecast, actual):
    mape = np.mean(np.abs(forecast - actual)/np.abs(actual))  # MAPE
    me = np.mean(forecast - actual)             # ME
    mae = np.mean(np.abs(forecast - actual))    # MAE
    mpe = np.mean((forecast - actual)/actual)   # MPE
    rmse = np.mean((forecast - actual)**2)**.5  # RMSE
    corr = np.corrcoef(forecast, actual)[0,1]   # corr
    mins = np.amin(np.hstack([forecast[:,None],
                              actual[:,None]]), axis=1)
    maxs = np.amax(np.hstack([forecast[:,None],
                              actual[:,None]]), axis=1)
    minmax = 1 - np.mean(mins/maxs)             # minmax
    acf1 = acf(forecast-actual)[1]                      # ACF1
    return({'mape':mape, 'me':me, 'mae': mae,
            'mpe': mpe, 'rmse':rmse, 'acf1':acf1,
            'corr':corr, 'minmax':minmax})

forecast_accuracy(test['temp'].values, forecast["temp_forecast"].values)

/usr/local/lib/python3.7/dist-packages/statsmodels/tsa/stattools.py:541: FutureWarning:

fft=True will become the default in a future version of statsmodels. To suppress this warning, explicitly set fft=False.



{'acf1': 0.8328665483671378,
 'corr': 0.24779657215567957,
 'mae': 0.30136883037144946,
 'mape': 0.015584040313177566,
 'me': 0.11048619034999595,
 'minmax': 0.01532715979845689,
 'mpe': 0.005708164412840347,
 'rmse': 0.3710714563983969}

In [ ]:
import pickle
from statsmodels.tsa.arima_model import ARIMAResults

In [ ]:
# save model
temp_model_fit.save('temp_model.pkl')
# load model
temperature_model_loaded = ARIMAResults.load('temp_model.pkl')

In [ ]:
#forecast
fc, se, conf = temperature_model_loaded.forecast(4321, alpha=0.05)

# #make as pandas series
# fc_Series = pd.Series(fc, index = future_index)

In [ ]:
fc

array([19.56630326, 19.56528601, 19.56427305, ..., 19.32493586,
       19.32493586, 19.32493586])

In [ ]:
test.temp

Datetime
2020-07-17 00:02:00    19.700001
2020-07-17 00:03:00    19.700001
2020-07-17 00:04:00    19.710001
2020-07-17 00:05:00    19.710001
2020-07-17 00:06:00    19.788888
                         ...    
2020-07-19 23:59:00    16.739999
2020-07-20 00:00:00    19.299999
2020-07-20 00:01:00    19.299999
2020-07-20 00:02:00    19.266666
2020-07-20 00:03:00    19.200001
Name: temp, Length: 4322, dtype: float64

In [ ]:
future_index = pd.date_range("2020-07-20 00:03:00", "2020-07-23 00:03:00", freq="Min")
future_index

DatetimeIndex(['2020-07-20 00:03:00', '2020-07-20 00:04:00',
               '2020-07-20 00:05:00', '2020-07-20 00:06:00',
               '2020-07-20 00:07:00', '2020-07-20 00:08:00',
               '2020-07-20 00:09:00', '2020-07-20 00:10:00',
               '2020-07-20 00:11:00', '2020-07-20 00:12:00',
               ...
               '2020-07-22 23:54:00', '2020-07-22 23:55:00',
               '2020-07-22 23:56:00', '2020-07-22 23:57:00',
               '2020-07-22 23:58:00', '2020-07-22 23:59:00',
               '2020-07-23 00:00:00', '2020-07-23 00:01:00',
               '2020-07-23 00:02:00', '2020-07-23 00:03:00'],
              dtype='datetime64[ns]', length=4321, freq='T')

In [ ]:
forecast_df = pd.DataFrame(fc, index=future_index, columns=["Temp"])
forecast_df

Temp
2020-07-20 00:03:00  19.566303
2020-07-20 00:04:00  19.565286
2020-07-20 00:05:00  19.564273
2020-07-20 00:06:00  19.563264
2020-07-20 00:07:00  19.562260
...                        ...
2020-07-22 23:59:00  19.324936
2020-07-23 00:00:00  19.324936
2020-07-23 00:01:00  19.324936
2020-07-23 00:02:00  19.324936
2020-07-23 00:03:00  19.324936

[4321 rows x 1 columns]

In [ ]:
fc =  pd.concat([df_copy["temp"],forecast_df["Temp"]], axis = 0, join="outer")
future_df = pd.DataFrame(fc.values,index=fc.index, columns=["Temp"])
future_df

Temp
2020-07-12 00:01:00  19.700001
2020-07-12 00:02:00  19.744445
2020-07-12 00:03:00  19.763636
2020-07-12 00:04:00  19.750000
2020-07-12 00:05:00  19.744445
...                        ...
2020-07-22 23:59:00  19.324936
2020-07-23 00:00:00  19.324936
2020-07-23 00:01:00  19.324936
2020-07-23 00:02:00  19.324936
2020-07-23 00:03:00  19.324936

[15844 rows x 1 columns]

In [ ]:
# pd.DataFrame(df_copy['temp']).merge(pd.DataFrame(forecast_df["temp"]),
#                             left_index=True, right_index=True, how='outer')

In [ ]:

fig = go.Figure()

# Add traces
fig.add_trace(go.Scatter(x=future_df.index, y=future_df["Temp"],
                    mode='lines+markers'))

fig.update_layout(
    title="Forecasted Temperature for next 3 days",
    xaxis_title="Days ",
    yaxis_title="Temperature",
    font=dict(
        family="Courier New, monospace",
        size=18,
        color="RebeccaPurple"
    )
)

fig.show()

# Humidity Model Training and forecasting

In [ ]:
from statsmodels.tsa.arima_model import ARIMA
humidity_model = ARIMA(train["humidity"], order = (1,0,1), freq="Min")
humidity_model_fit = humidity_model.fit()

In [ ]:
humidity_model_fit.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                              ARMA Model Results                              
==============================================================================
Dep. Variable:               humidity   No. Observations:                 7201
Model:                     ARMA(1, 1)   Log Likelihood               -6152.708
Method:                       css-mle   S.D. of innovations              0.569
Date:                Mon, 12 Jul 2021   AIC                          12313.416
Time:                        09:38:58   BIC                          12340.944
Sample:                    07-12-2020   HQIC                         12322.888
                         - 07-17-2020                                         
==================================================================================
                     coef    std err          z      P>|z|      [0.025      0.975]
----------------------------------------------------------------------------------
const             74.7866      0.133    563.709      0.000      74.527      75.047
ar.L1.humidity     0.9770      0.003    356.600      0.000       0.972       0.982
ma.L1.humidity    -0.5429      0.012    -46.658      0.000      -0.566      -0.520
                                    Roots                                    
=============================================================================
                  Real          Imaginary           Modulus         Frequency
-----------------------------------------------------------------------------
AR.1            1.0235           +0.0000j            1.0235            0.0000
MA.1            1.8421           +0.0000j            1.8421            0.0000
-----------------------------------------------------------------------------
"""

In [ ]:
hum_forecast = pd.DataFrame(humidity_model_fit.predict(start=7201, end = 11522),columns=['hum_Prediction'])
hum_forecast

hum_Prediction
2020-07-17 00:02:00       74.725025
2020-07-17 00:03:00       74.726438
2020-07-17 00:04:00       74.727818
2020-07-17 00:05:00       74.729166
2020-07-17 00:06:00       74.730483
...                             ...
2020-07-19 23:59:00       74.786557
2020-07-20 00:00:00       74.786557
2020-07-20 00:01:00       74.786557
2020-07-20 00:02:00       74.786557
2020-07-20 00:03:00       74.786557

[4322 rows x 1 columns]

In [ ]:
forecasted_df[['humidity',"hum_Prediction" ]] = pd.concat([test['humidity'],hum_forecast["hum_Prediction"]], axis=1, join="inner")

In [ ]:
forecasted_df

temp  temp_forecast   humidity  hum_Prediction
2020-07-17 00:02:00  19.700001      19.566303  74.850002       74.725025
2020-07-17 00:03:00  19.700001      19.565286  75.020000       74.726438
2020-07-17 00:04:00  19.710001      19.564273  75.030000       74.727818
2020-07-17 00:05:00  19.710001      19.563264  75.030000       74.729166
2020-07-17 00:06:00  19.788888      19.562260  75.022222       74.730483
...                        ...            ...        ...             ...
2020-07-19 23:59:00  16.739999      19.324936  70.479999       74.786557
2020-07-20 00:00:00  19.299999      19.324936  75.500000       74.786557
2020-07-20 00:01:00  19.299999      19.324936  75.370002       74.786557
2020-07-20 00:02:00  19.266666      19.324936  75.383335       74.786557
2020-07-20 00:03:00  19.200001      19.324936  75.342860       74.786557

[4322 rows x 4 columns]

In [ ]:

fig = go.Figure()

# Add traces
fig.add_trace(go.Scatter(x=forecasted_df.index , y=forecasted_df["humidity"],
                    mode='lines+markers',
                     name='Actual Humidity '))
fig.add_trace(go.Scatter(x=forecasted_df.index  , y= forecasted_df["hum_Prediction"],
                     mode='lines+markers',
                     name='Forecasted Humidity'))


fig.update_layout(
    title="Actual Vs Forecasted Humidity ",
    xaxis_title="Days ",
    yaxis_title= "Humidity",
    font=dict(
        family="Courier New, monospace",
        size=18,
        color="RebeccaPurple"
    )
)

fig.show()

In [ ]:

forecast_accuracy(forecasted_df['humidity'].values, forecasted_df["hum_Prediction"].values)

/usr/local/lib/python3.7/dist-packages/statsmodels/tsa/stattools.py:541: FutureWarning:

fft=True will become the default in a future version of statsmodels. To suppress this warning, explicitly set fft=False.



{'acf1': 0.8380933649699195,
 'corr': 0.2320415870497941,
 'mae': 1.7743594719338769,
 'mape': 0.023725687582398437,
 'me': 1.6901503246605176,
 'minmax': 0.02301666350245435,
 'mpe': 0.022599635618358087,
 'rmse': 2.0497524371033573}

In [ ]:
# save model
humidity_model_fit.save('humidity_model.pkl')
# load model
humidity_model_loaded = ARIMAResults.load('humidity_model.pkl')

In [ ]:
# forecast_hum = humidity_model_loaded.predict(start=11523, end = 15844)
# future_df["Humidity"] = forecast_hum.values

In [ ]:
#forecast
fc, se, conf = humidity_model_loaded.forecast(4321, alpha=0.05)

forecast_df["humidity"] = fc
forecast_df

Temp  humidity    humidity
2020-07-20 00:03:00  19.566303  74.725025  74.725025
2020-07-20 00:04:00  19.565286  74.726438  74.726438
2020-07-20 00:05:00  19.564273  74.727818  74.727818
2020-07-20 00:06:00  19.563264  74.729166  74.729166
2020-07-20 00:07:00  19.562260  74.730483  74.730483
...                        ...        ...        ...
2020-07-22 23:59:00  19.324936  74.786557  74.786557
2020-07-23 00:00:00  19.324936  74.786557  74.786557
2020-07-23 00:01:00  19.324936  74.786557  74.786557
2020-07-23 00:02:00  19.324936  74.786557  74.786557
2020-07-23 00:03:00  19.324936  74.786557  74.786557

[4321 rows x 3 columns]

In [ ]:
pd.concat([df_copy["humidity"],forecast_df["humidity"]], axis = 0, join="outer")

2020-07-12 00:01:00    76.000000
2020-07-12 00:02:00    75.933334
2020-07-12 00:03:00    76.063635
2020-07-12 00:04:00    76.091665
2020-07-12 00:05:00    76.288888
                         ...    
2020-07-22 23:59:00    74.786557
2020-07-23 00:00:00    74.786557
2020-07-23 00:01:00    74.786557
2020-07-23 00:02:00    74.786557
2020-07-23 00:03:00    74.786557
Name: humidity, Length: 15844, dtype: float64

In [ ]:
fc =  pd.concat([df_copy["humidity"],forecast_df["humidity"]], axis = 0, join="outer")
future_df["humidity"] = fc
future_df

Temp   humidity
2020-07-12 00:01:00  19.700001  76.000000
2020-07-12 00:02:00  19.744445  75.933334
2020-07-12 00:03:00  19.763636  76.063635
2020-07-12 00:04:00  19.750000  76.091665
2020-07-12 00:05:00  19.744445  76.288888
...                        ...        ...
2020-07-22 23:59:00  19.324936  74.786557
2020-07-23 00:00:00  19.324936  74.786557
2020-07-23 00:01:00  19.324936  74.786557
2020-07-23 00:02:00  19.324936  74.786557
2020-07-23 00:03:00  19.324936  74.786557

[15844 rows x 2 columns]

In [ ]:
future_df

Temp   humidity
2020-07-12 00:01:00  19.700001  76.000000
2020-07-12 00:02:00  19.744445  75.933334
2020-07-12 00:03:00  19.763636  76.063635
2020-07-12 00:04:00  19.750000  76.091665
2020-07-12 00:05:00  19.744445  76.288888
...                        ...        ...
2020-07-22 23:59:00  19.324936  74.786557
2020-07-23 00:00:00  19.324936  74.786557
2020-07-23 00:01:00  19.324936  74.786557
2020-07-23 00:02:00  19.324936  74.786557
2020-07-23 00:03:00  19.324936  74.786557

[15844 rows x 2 columns]

In [ ]:

fig = go.Figure()

# Add traces
fig.add_trace(go.Scatter(x=future_df.index, y=future_df["humidity"],
                    mode='lines+markers'))

fig.update_layout(
    title="Forecasted Humidity for next 3 days",
    xaxis_title="Days ",
    yaxis_title="Humidity",
    font=dict(
        family="Courier New, monospace",
        size=18,
        color="RebeccaPurple"
    )
)

fig.show()

# Co Model Training and forecasting

In [ ]:
co_model = ARIMA(train["co"], order = (1,0,1), freq="Min")
co_model_fit = co_model.fit()

In [ ]:
co_model_fit.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                              ARMA Model Results                              
==============================================================================
Dep. Variable:                     co   No. Observations:                 7201
Model:                     ARMA(1, 1)   Log Likelihood               62687.212
Method:                       css-mle   S.D. of innovations              0.000
Date:                Mon, 12 Jul 2021   AIC                        -125366.425
Time:                        09:51:10   BIC                        -125338.897
Sample:                    07-12-2020   HQIC                       -125356.953
                         - 07-17-2020                                         
==============================================================================
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
const          0.0033      0.001      3.302      0.001       0.001       0.005
ar.L1.co       0.9996      0.000   3927.812      0.000       0.999       1.000
ma.L1.co       0.0103      0.010      1.012      0.312      -0.010       0.030
                                    Roots                                    
=============================================================================
                  Real          Imaginary           Modulus         Frequency
-----------------------------------------------------------------------------
AR.1            1.0004           +0.0000j            1.0004            0.0000
MA.1          -97.1989           +0.0000j           97.1989            0.5000
-----------------------------------------------------------------------------
"""

In [ ]:
co_forecast = pd.DataFrame(co_model_fit.predict(start=7201, end = 11522),columns=['co_Prediction'])
co_forecast

co_Prediction
2020-07-17 00:02:00       0.002281
2020-07-17 00:03:00       0.002281
2020-07-17 00:04:00       0.002282
2020-07-17 00:05:00       0.002282
2020-07-17 00:06:00       0.002283
...                            ...
2020-07-19 23:59:00       0.003121
2020-07-20 00:00:00       0.003121
2020-07-20 00:01:00       0.003121
2020-07-20 00:02:00       0.003121
2020-07-20 00:03:00       0.003121

[4322 rows x 1 columns]

In [ ]:
forecasted_df[['co',"co_Prediction" ]] = pd.concat([test['co'],co_forecast["co_Prediction"]], axis=1, join="inner")
forecasted_df

temp  temp_forecast  ...        co  co_Prediction
2020-07-17 00:02:00  19.700001      19.566303  ...  0.002271       0.002281
2020-07-17 00:03:00  19.700001      19.565286  ...  0.002261       0.002281
2020-07-17 00:04:00  19.710001      19.564273  ...  0.002254       0.002282
2020-07-17 00:05:00  19.710001      19.563264  ...  0.002252       0.002282
2020-07-17 00:06:00  19.788888      19.562260  ...  0.002248       0.002283
...                        ...            ...  ...       ...            ...
2020-07-19 23:59:00  16.739999      19.324936  ...  0.003745       0.003121
2020-07-20 00:00:00  19.299999      19.324936  ...  0.003743       0.003121
2020-07-20 00:01:00  19.299999      19.324936  ...  0.003747       0.003121
2020-07-20 00:02:00  19.266666      19.324936  ...  0.003747       0.003121
2020-07-20 00:03:00  19.200001      19.324936  ...  0.003749       0.003121

[4322 rows x 6 columns]

In [ ]:

fig = go.Figure()

# Add traces
fig.add_trace(go.Scatter(x=forecasted_df.index , y=forecasted_df["co"],
                    mode='lines+markers',
                     name='Actual Co '))
fig.add_trace(go.Scatter(x=forecasted_df.index  , y= forecasted_df["co_Prediction"],
                     mode='lines+markers',
                     name='Forecasted Co'))


fig.update_layout(
    title="Actual Vs Forecasted Co ",
    xaxis_title="Days ",
    yaxis_title= "Co",
    font=dict(
        family="Courier New, monospace",
        size=18,
        color="RebeccaPurple"
    )
)

fig.show()

In [ ]:
forecast_accuracy(forecasted_df['co'].values, forecasted_df["co_Prediction"].values)

/usr/local/lib/python3.7/dist-packages/statsmodels/tsa/stattools.py:541: FutureWarning:

fft=True will become the default in a future version of statsmodels. To suppress this warning, explicitly set fft=False.



{'acf1': 0.9996578645714012,
 'corr': 0.5037876927132453,
 'mae': 0.0007566446357541137,
 'mape': 0.2731900555022206,
 'me': 0.0001081080054442055,
 'minmax': 0.22602381804781202,
 'mpe': 0.028926478404814177,
 'rmse': 0.0009338908711432514}

In [ ]:
# save model
co_model_fit.save('co_model.pkl')
# load model
co_model_loaded = ARIMAResults.load('co_model.pkl')

In [ ]:
# forecast_co = co_model_loaded.predict(start=1, end = 4321)
# future_df["co"] = forecast_co.values

In [ ]:
#forecast
fc, se, conf = co_model_loaded.forecast(4321, alpha=0.05)

forecast_df["co"] = fc
# forecast_df

fc =  pd.concat([df_copy["co"],forecast_df["co"]], axis = 0, join="outer")
future_df["co"] = fc
future_df

Temp   humidity        co
2020-07-12 00:01:00  19.700001  76.000000  0.002889
2020-07-12 00:02:00  19.744445  75.933334  0.002880
2020-07-12 00:03:00  19.763636  76.063635  0.002867
2020-07-12 00:04:00  19.750000  76.091665  0.002838
2020-07-12 00:05:00  19.744445  76.288888  0.002851
...                        ...        ...       ...
2020-07-22 23:59:00  19.324936  74.786557  0.003121
2020-07-23 00:00:00  19.324936  74.786557  0.003121
2020-07-23 00:01:00  19.324936  74.786557  0.003121
2020-07-23 00:02:00  19.324936  74.786557  0.003121
2020-07-23 00:03:00  19.324936  74.786557  0.003121

[15844 rows x 3 columns]

In [ ]:
future_df

Temp   humidity        co
2020-07-12 00:01:00  19.700001  76.000000  0.002889
2020-07-12 00:02:00  19.744445  75.933334  0.002880
2020-07-12 00:03:00  19.763636  76.063635  0.002867
2020-07-12 00:04:00  19.750000  76.091665  0.002838
2020-07-12 00:05:00  19.744445  76.288888  0.002851
...                        ...        ...       ...
2020-07-22 23:59:00  19.324936  74.786557  0.003121
2020-07-23 00:00:00  19.324936  74.786557  0.003121
2020-07-23 00:01:00  19.324936  74.786557  0.003121
2020-07-23 00:02:00  19.324936  74.786557  0.003121
2020-07-23 00:03:00  19.324936  74.786557  0.003121

[15844 rows x 3 columns]

In [ ]:

fig = go.Figure()

# Add traces
fig.add_trace(go.Scatter(x=future_df.index, y=future_df["co"],
                    mode='lines+markers'))

fig.update_layout(
    title="Forecasted Co for next 3 days",
    xaxis_title="Days ",
    yaxis_title="Co",
    font=dict(
        family="Courier New, monospace",
        size=18,
        color="RebeccaPurple"
    )
)

fig.show()

# Conclusion

* The ARIMA model for Temperature, Humidity and Co shows an co-relation of 0.24 , 0.23 and 0.50 respectivelty which indicates the co-relation between the actual and predicted values and a very High value for mape for each model

* The Forecast for next 3 days from the saved model is not able to trace the previousse trend and patterns.

*  For this data set and this parameters ARIMA model will be a good option.

# Reference Links

[Plotly Charts](https://plotly.com/python/line-and-scatter/#scatter-plot-with-plotly-express)

[ARIMA Model and Time Series ](https://www.machinelearningplus.com/time-series/arima-model-time-series-forecasting-python/)

[Time Series Codes](https://github.com/srivatsan88/End-to-End-Time-Series)